# model TPH

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime
from datetime import timedelta
import re
from dateutil.parser import parse
import string
import warnings
warnings.filterwarnings('ignore')
import plotly.graph_objects as go
from sklearn.metrics import mean_absolute_percentage_error
import missingno as msno
from plotly.subplots import make_subplots
from sklearn.preprocessing import MinMaxScaler
import scipy
import researchpy as rp
from matplotlib.offsetbox import AnchoredText
#import pacmap
from sklearn.compose import ColumnTransformer
from sklearn.cluster import KMeans
from sklearn.pipeline import Pipeline
import plotly.express as px
from sklearn.metrics import r2_score
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestRegressor
from imblearn.over_sampling import RandomOverSampler
from sklearn.model_selection import train_test_split 
# Import Halving Grid Search
from sklearn.experimental import enable_halving_search_cv 
from sklearn.model_selection import HalvingGridSearchCV
import xgboost as xgb
from scipy.stats import kurtosis,skew
from numpy import mean,sqrt,square
from scipy.fftpack import fft, fftfreq
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import PredefinedSplit
sns.set_style("darkgrid")
pd.set_option('display.max_columns', None)
pd.options.display.max_colwidth = 100

In [2]:
# Función que filtra tags por alta correlación
def corrkill(dataframe, features, corr_cut=0.8):

    df = dataframe[features]
    dfcorr = pd.DataFrame(np.triu(df.corr()), columns=df.columns, index=df.columns)
    dfcorr = dfcorr.stack().reset_index()
    dfcorr.columns = ['Feat1','Feat2','Val']
    dfcorr = dfcorr[~dfcorr['Val'].isin([0,1])]
    dfcorr = dfcorr[dfcorr['Val'].abs()>corr_cut]
    dfcorr["Val"]=dfcorr["Val"].abs()
    
    return list(dfcorr['Feat2']), dfcorr.sort_values(by="Val",ascending=False)

In [3]:
variables_interes=['pyrite law', 'chalcopyrite law',
       'chalcocite law', 'covelin law', 'crusher index', 'sag power index',
       'ball work index', 'bornite law','charge cell', 'TPH','water', 'speed','HH TPH', 'granulometry', 'Edad','loss of TPH',
       "power","solid percentage","HH charge cell","LL charge cell","delta HH TPH","delta HH charge cell","delta LL charge cell"]
variables_interes

['pyrite law',
 'chalcopyrite law',
 'chalcocite law',
 'covelin law',
 'crusher index',
 'sag power index',
 'ball work index',
 'bornite law',
 'charge cell',
 'TPH',
 'water',
 'speed',
 'HH TPH',
 'granulometry',
 'Edad',
 'loss of TPH',
 'power',
 'solid percentage',
 'HH charge cell',
 'LL charge cell',
 'delta HH TPH',
 'delta HH charge cell',
 'delta LL charge cell']

In [4]:
# read
tags=pd.read_excel("../../../data/meta data/tags relevantes.xlsx")
tags_cc=tags.tag.to_list()
dic={}
for i,j in zip(tags.tag,tags.description):
    dic[i]=j

In [5]:
# Se lee csv
liners_age=pd.read_csv('../../../data/consolidated data/liners_age_03January2022.csv', parse_dates=['Timestamp'], index_col='Timestamp')
# Se lee csv
cleaned=pd.read_csv('../../../data/consolidated data/cleaned_15December2022.csv', parse_dates=['Timestamp'], index_col='Timestamp')
cleaned.sort_index(inplace=True)
cleaned.rename(columns=dic,inplace=True)
df_cleaned_age=cleaned.join(liners_age).dropna()
df_cleaned_age["delta HH TPH"]=df_cleaned_age["HH TPH"]-df_cleaned_age["TPH"]
df_cleaned_age["delta HH charge cell"]=df_cleaned_age["HH charge cell"]-df_cleaned_age["charge cell"]
df_cleaned_age["delta LL charge cell"]=df_cleaned_age["charge cell"]-df_cleaned_age["LL charge cell"]
df_cleaned_age["loss of TPH"]=df_cleaned_age["delta HH TPH"].apply(lambda x: 1 if x>100 else 0)
df_cleaned_age=df_cleaned_age[variables_interes]
df_cleaned_age.head()

pyrite law  chalcopyrite law  chalcocite law  \
Timestamp                                                           
2020-01-10 01:00:00         2.3              1.76             0.5   
2020-01-10 01:01:00         2.3              1.76             0.5   
2020-01-10 01:02:00         2.3              1.76             0.5   
2020-01-10 01:03:00         2.3              1.76             0.5   
2020-01-10 01:04:00         2.3              1.76             0.5   

                     covelin law  crusher index  sag power index  \
Timestamp                                                          
2020-01-10 01:00:00         0.02        19.7649          98.5569   
2020-01-10 01:01:00         0.02        19.7649          98.5569   
2020-01-10 01:02:00         0.02        19.7649          98.5569   
2020-01-10 01:03:00         0.02        19.7649          98.5569   
2020-01-10 01:04:00         0.02        19.7649          98.5569   

                     ball work index  bornite law  charge cell          TPH  \
Timestamp                                                                     
2020-01-10 01:00:00          15.4504         0.05   823.909536  4095.626634   
2020-01-10 01:01:00          15.4504         0.05   824.839407  4065.884243   
2020-01-10 01:02:00          15.4504         0.05   824.649549  4030.786580   
2020-01-10 01:03:00          15.4504         0.05   823.890193  4018.548119   
2020-01-10 01:04:00          15.4504         0.05   822.616814  4031.546547   

                           water     speed  HH TPH  granulometry  Edad  \
Timestamp                                                                
2020-01-10 01:00:00  1543.366447  9.250491  4100.0     42.290517   1.0   
2020-01-10 01:01:00  1550.973678  9.258654  4100.0     42.224897   1.0   
2020-01-10 01:02:00  1565.958666  9.250667  4100.0     42.235243   1.0   
2020-01-10 01:03:00  1570.175300  9.310925  4100.0     42.256266   1.0   
2020-01-10 01:04:00  1584.178107  9.312753  4100.0     42.283309   1.0   

                     loss of TPH         power  solid percentage  \
Timestamp                                                          
2020-01-10 01:00:00            0  22603.234708         72.612950   
2020-01-10 01:01:00            0  22625.327947         72.431979   
2020-01-10 01:02:00            0  22646.748972         72.010136   
2020-01-10 01:03:00            0  22741.929035         71.944631   
2020-01-10 01:04:00            0  22762.649082         71.787584   

                     HH charge cell  LL charge cell  delta HH TPH  \
Timestamp                                                           
2020-01-10 01:00:00           850.0           770.0      4.373366   
2020-01-10 01:01:00           850.0           770.0     34.115757   
2020-01-10 01:02:00           850.0           770.0     69.213420   
2020-01-10 01:03:00           850.0           770.0     81.451881   
2020-01-10 01:04:00           850.0           770.0     68.453453   

                     delta HH charge cell  delta LL charge cell  
Timestamp                                                        
2020-01-10 01:00:00             26.090464             53.909536  
2020-01-10 01:01:00             25.160593             54.839407  
2020-01-10 01:02:00             25.350451             54.649549  
2020-01-10 01:03:00             26.109807             53.890193  
2020-01-10 01:04:00             27.383186             52.616814

In [6]:
df_cleaned_age["TPH"]

Timestamp
2020-01-10 01:00:00    4095.626634
2020-01-10 01:01:00    4065.884243
2020-01-10 01:02:00    4030.786580
2020-01-10 01:03:00    4018.548119
2020-01-10 01:04:00    4031.546547
                          ...     
2022-02-28 11:58:00    2713.765821
2022-02-28 11:59:00    2695.889244
2022-02-28 12:00:00    2718.401757
2022-02-28 12:01:00    2694.856279
2022-02-28 12:02:00    2705.770205
Name: TPH, Length: 859344, dtype: float64

In [11]:
df_cleaned_age["TPH"].ewm(span=5,min_periods=0,ignore_na=True).mean()

Timestamp
2020-01-10 01:00:00    4095.626634
2020-01-10 01:01:00    4077.781200
2020-01-10 01:02:00    4055.520590
2020-01-10 01:03:00    4040.162795
2020-01-10 01:04:00    4036.855136
                          ...     
2022-02-28 11:58:00    2698.221098
2022-02-28 11:59:00    2697.443813
2022-02-28 12:00:00    2704.429795
2022-02-28 12:01:00    2701.238623
2022-02-28 12:02:00    2702.749150
Name: TPH, Length: 859344, dtype: float64

In [ ]:
df_corr = df_cleaned_age.dropna().corr()
corr_tph=pd.DataFrame(df_corr.abs().TPH.sort_values(ascending=False))
top_corr=corr_tph[corr_tph.TPH>=0]
top_corr

# Feature Engineering

In [ ]:
def feature_engineering(df):
      
    targets = ["TPH","Edad","loss of TPH","HH TPH"]
    df_vars = df.copy()
    column_inicial=df_vars.columns

    for column in df_vars:
    
        if (column not in targets):

            ## 10 min
            #df_vars[f"skew_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:skew(x))
            #df_vars[f"kurt_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:kurtosis(x))
            df_vars[f"mean_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:np.nanmean(list(x)))
            df_vars[f"max_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:np.nanmax(list(x)))
            #df_vars[f"sum_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:np.nansum(list(x)))
            df_vars[f"min_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x:np.nanmin(list(x)))
            df_vars[f"rms_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x: sqrt(mean(square(list(x)))))
            df_vars[f"var_{column}_10"]=df_vars[column].rolling(window=10).apply(lambda x: np.nanvar(x))

            # 5 min
            df_vars[f"mean_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x:np.nanmean(list(x)))
            df_vars[f"max_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x:np.nanmax(list(x)))
            #df_vars[f"sum_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x:np.nansum(list(x)))
            df_vars[f"min_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x:np.nanmin(list(x)))
            df_vars[f"rms_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x: sqrt(mean(square(list(x)))))
            df_vars[f"var_{column}_5"]=df_vars[column].rolling(window=5).apply(lambda x: np.nanvar(x))

            # 3 min
            #df_vars[f"skew_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:skew(x))
            #df_vars[f"kurt_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:kurtosis(x))
            df_vars[f"mean_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:np.nanmean(list(x)))
            df_vars[f"max_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:np.nanmax(list(x)))
            #df_vars[f"sum_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:np.nansum(list(x)))
            df_vars[f"min_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x:np.nanmin(list(x)))
            df_vars[f"rms_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x: sqrt(mean(square(list(x)))))
            df_vars[f"var_{column}_3"]=df_vars[column].rolling(window=3).apply(lambda x: np.nanvar(x))
          

    for column in column_inicial:

        if (column not in targets):
            
            # lags  
            df_vars[f"{column}_(t-1)"] = df_vars[column].shift(1)
            df_vars[f'{column}_(t-2)'] = df_vars[column].shift(2)
            df_vars[f'{column}_(t-3)'] = df_vars[column].shift(3)
            df_vars[f'{column}_(t-4)'] = df_vars[column].shift(4)
            df_vars[f'{column}_(t-5)'] = df_vars[column].shift(5)
           
    
    return df_vars
   

In [ ]:
df_features=feature_engineering(df_cleaned_age)

In [ ]:
# Se guarda en csv
df_features.to_csv('../../../data/processed data/df_feature_engineering_'+pd.to_datetime('today').strftime('%d%B%Y')+'.csv', index=True)

In [ ]:
df_features.shape

In [14]:
# Age tph processed
liners_age=pd.read_csv('../../../data/consolidated data/liners_age_03January2023.csv', parse_dates=['Timestamp'], index_col='Timestamp')
liners_age.head()

age tph processed
Timestamp                             
2018-01-01 00:00:00        3847.009774
2018-01-01 00:01:00        7720.005775
2018-01-01 00:02:00       11599.216924
2018-01-01 00:03:00       15494.009869
2018-01-01 00:04:00       19453.426716

In [15]:
liners_age.shape

(2475480, 1)

In [12]:
# read df full csv
df_features0=pd.read_csv('../../../data/processed data/df_feature_engineering_18December2022.csv', parse_dates=['Timestamp'], index_col='Timestamp')#["2020":"2021"]
df_features0["TPH"]=df_features0["TPH"].shift(-10)
df_features0["loss of TPH"]=df_features0["loss of TPH"].shift(-10)
df_features0.dropna(inplace=True)
df_features0.sort_index(inplace=True)
df_features0.shape

(859325, 403)

In [18]:
# Verificando si hay duplicados
u=[i for i in df_features0.columns if (not re.match(".*water",i)) and (not re.match(".*power",i)) and (not re.match(".*delta HH TPH",i)) ]
y=[i for i in df_features0.columns if  re.match(".*sag power index",i)] 
u=y+u
df_features=df_features0[u].copy().join(liners_age).drop(columns=["Edad"])
df_features.head(1)

sag power index  mean_sag power index_10  \
Timestamp                                                       
2020-01-10 01:09:00          98.5569                  98.5569   

                     max_sag power index_10  min_sag power index_10  \
Timestamp                                                             
2020-01-10 01:09:00                 98.5569                 98.5569   

                     rms_sag power index_10  var_sag power index_10  \
Timestamp                                                             
2020-01-10 01:09:00                 98.5569            2.019484e-28   

                     mean_sag power index_5  max_sag power index_5  \
Timestamp                                                            
2020-01-10 01:09:00                 98.5569                98.5569   

                     min_sag power index_5  rms_sag power index_5  \
Timestamp                                                           
2020-01-10 01:09:00                98.5569                98.5569   

                     var_sag power index_5  mean_sag power index_3  \
Timestamp                                                            
2020-01-10 01:09:00                    0.0                 98.5569   

                     max_sag power index_3  min_sag power index_3  \
Timestamp                                                           
2020-01-10 01:09:00                98.5569                98.5569   

                     rms_sag power index_3  var_sag power index_3  \
Timestamp                                                           
2020-01-10 01:09:00                98.5569                    0.0   

                     sag power index_(t-1)  sag power index_(t-2)  \
Timestamp                                                           
2020-01-10 01:09:00                98.5569                98.5569   

                     sag power index_(t-3)  sag power index_(t-4)  \
Timestamp                                                           
2020-01-10 01:09:00                98.5569                98.5569   

                     sag power index_(t-5)  pyrite law  chalcopyrite law  \
Timestamp                                                                  
2020-01-10 01:09:00                98.5569         2.3              1.76   

                     chalcocite law  covelin law  crusher index  \
Timestamp                                                         
2020-01-10 01:09:00             0.5         0.02        19.7649   

                     ball work index  bornite law  charge cell          TPH  \
Timestamp                                                                     
2020-01-10 01:09:00          15.4504         0.05   820.483684  4102.411862   

                        speed  HH TPH  granulometry  loss of TPH  \
Timestamp                                                          
2020-01-10 01:09:00  9.312051  4100.0     42.044058          0.0   

                     solid percentage  HH charge cell  LL charge cell  \
Timestamp                                                               
2020-01-10 01:09:00         71.462459           850.0           770.0   

                     delta HH charge cell  delta LL charge cell  \
Timestamp                                                         
2020-01-10 01:09:00             29.516316             50.483684   

                     mean_pyrite law_10  max_pyrite law_10  min_pyrite law_10  \
Timestamp                                                                       
2020-01-10 01:09:00                 2.3                2.3                2.3   

                     rms_pyrite law_10  var_pyrite law_10  mean_pyrite law_5  \
Timestamp                                                                      
2020-01-10 01:09:00                2.3                0.0                2.3   

                     max_pyrite law_5  min_pyrite law_5  rms_pyrite law_5  \
Timestamp                                                                   


# Correlación entre variables

In [19]:
# Se obtienen tags altamente correlacionados y matriz que permite visualizar cuales son los par de tags altamente correlacionados
collinearity, table_cor=corrkill(df_features,df_features.columns)

In [20]:
# Tags altamente correlacionados
table_cor

Feat1                        Feat2       Val
72977        mean_HH charge cell_3         rms_HH charge cell_3  1.000000
78092        mean_LL charge cell_3         rms_LL charge cell_3  1.000000
71272        mean_HH charge cell_5         rms_HH charge cell_5  1.000000
76387        mean_LL charge cell_5         rms_LL charge cell_5  1.000000
52517           mean_charge cell_3            rms_charge cell_3  1.000000
...                            ...                          ...       ...
80150  max_delta HH charge cell_10  max_delta LL charge cell_10  0.881337
80491  min_delta HH charge cell_10  min_delta LL charge cell_10  0.881317
52278            var_charge cell_5   var_delta LL charge cell_5  0.872349
52263            var_charge cell_5   var_delta HH charge cell_5  0.870536
53983            var_charge cell_3   var_delta LL charge cell_3  0.800245

[3656 rows x 3 columns]

In [21]:
df_corr = df_features.dropna().corr()
corr_tph=pd.DataFrame(df_corr.abs().TPH.sort_values(ascending=False))


In [22]:
top_corr=corr_tph[corr_tph.TPH>=0.2]
top_corr

TPH
TPH                      1.000000
HH TPH                   0.639734
loss of TPH              0.583261
min_solid percentage_10  0.344294
min_solid percentage_5   0.344096
...                           ...
max_crusher index_3      0.219464
max_crusher index_5      0.218945
max_crusher index_10     0.217686
max_charge cell_10       0.214084
max_charge cell_5        0.203449

[62 rows x 1 columns]

# Equilibrio de eventos de perdidas de TPH

In [26]:
# Entrenamiento
entrenamiento=pd.concat([df_features["2020-01":"2020-03"],df_features["2020-05"],df_features["2020-07":"2020-12"],df_features["2021-01":"2021-08"],df_features["2021-10"],df_features["2021-12"]])
entrenamiento.head(1)

sag power index  mean_sag power index_10  \
Timestamp                                                       
2020-01-10 01:09:00          98.5569                  98.5569   

                     max_sag power index_10  min_sag power index_10  \
Timestamp                                                             
2020-01-10 01:09:00                 98.5569                 98.5569   

                     rms_sag power index_10  var_sag power index_10  \
Timestamp                                                             
2020-01-10 01:09:00                 98.5569            2.019484e-28   

                     mean_sag power index_5  max_sag power index_5  \
Timestamp                                                            
2020-01-10 01:09:00                 98.5569                98.5569   

                     min_sag power index_5  rms_sag power index_5  \
Timestamp                                                           
2020-01-10 01:09:00                98.5569                98.5569   

                     var_sag power index_5  mean_sag power index_3  \
Timestamp                                                            
2020-01-10 01:09:00                    0.0                 98.5569   

                     max_sag power index_3  min_sag power index_3  \
Timestamp                                                           
2020-01-10 01:09:00                98.5569                98.5569   

                     rms_sag power index_3  var_sag power index_3  \
Timestamp                                                           
2020-01-10 01:09:00                98.5569                    0.0   

                     sag power index_(t-1)  sag power index_(t-2)  \
Timestamp                                                           
2020-01-10 01:09:00                98.5569                98.5569   

                     sag power index_(t-3)  sag power index_(t-4)  \
Timestamp                                                           
2020-01-10 01:09:00                98.5569                98.5569   

                     sag power index_(t-5)  pyrite law  chalcopyrite law  \
Timestamp                                                                  
2020-01-10 01:09:00                98.5569         2.3              1.76   

                     chalcocite law  covelin law  crusher index  \
Timestamp                                                         
2020-01-10 01:09:00             0.5         0.02        19.7649   

                     ball work index  bornite law  charge cell          TPH  \
Timestamp                                                                     
2020-01-10 01:09:00          15.4504         0.05   820.483684  4102.411862   

                        speed  HH TPH  granulometry  loss of TPH  \
Timestamp                                                          
2020-01-10 01:09:00  9.312051  4100.0     42.044058          0.0   

                     solid percentage  HH charge cell  LL charge cell  \
Timestamp                                                               
2020-01-10 01:09:00         71.462459           850.0           770.0   

                     delta HH charge cell  delta LL charge cell  \
Timestamp                                                         
2020-01-10 01:09:00             29.516316             50.483684   

                     mean_pyrite law_10  max_pyrite law_10  min_pyrite law_10  \
Timestamp                                                                       
2020-01-10 01:09:00                 2.3                2.3                2.3   

                     rms_pyrite law_10  var_pyrite law_10  mean_pyrite law_5  \
Timestamp                                                                      
2020-01-10 01:09:00                2.3                0.0                2.3   

                     max_pyrite law_5  min_pyrite law_5  rms_pyrite law_5  \
Timestamp                                                                   


In [27]:
# Validación
validacion=pd.concat([df_features["2020-06"],df_features["2021-11"]])
validacion.head(1)

sag power index  mean_sag power index_10  max_sag power index_10  \
Timestamp                                                                      
2020-06-01            183.0                    183.0                   183.0   

            min_sag power index_10  rms_sag power index_10  \
Timestamp                                                    
2020-06-01                   183.0                   183.0   

            var_sag power index_10  mean_sag power index_5  \
Timestamp                                                    
2020-06-01                     0.0                   183.0   

            max_sag power index_5  min_sag power index_5  \
Timestamp                                                  
2020-06-01                  183.0                  183.0   

            rms_sag power index_5  var_sag power index_5  \
Timestamp                                                  
2020-06-01                  183.0                    0.0   

            mean_sag power index_3  max_sag power index_3  \
Timestamp                                                   
2020-06-01                   183.0                  183.0   

            min_sag power index_3  rms_sag power index_3  \
Timestamp                                                  
2020-06-01                  183.0                  183.0   

            var_sag power index_3  sag power index_(t-1)  \
Timestamp                                                  
2020-06-01                    0.0                  183.0   

            sag power index_(t-2)  sag power index_(t-3)  \
Timestamp                                                  
2020-06-01                  183.0                  183.0   

            sag power index_(t-4)  sag power index_(t-5)  pyrite law  \
Timestamp                                                              
2020-06-01                  183.0                  183.0        0.82   

            chalcopyrite law  chalcocite law  covelin law  crusher index  \
Timestamp                                                                  
2020-06-01              0.82            0.41          0.0           23.8   

            ball work index  bornite law  charge cell          TPH     speed  \
Timestamp                                                                      
2020-06-01             18.4          0.0   811.822555  3553.885205  8.877953   

            HH TPH  granulometry  loss of TPH  solid percentage  \
Timestamp                                                         
2020-06-01  4400.0      52.80404          1.0         65.044377   

            HH charge cell  LL charge cell  delta HH charge cell  \
Timestamp                                                          
2020-06-01           820.0           740.0              8.177445   

            delta LL charge cell  mean_pyrite law_10  max_pyrite law_10  \
Timestamp                                                                 
2020-06-01             71.822555                0.82               0.82   

            min_pyrite law_10  rms_pyrite law_10  var_pyrite law_10  \
Timestamp                                                             
2020-06-01               0.82               0.82                0.0   

            mean_pyrite law_5  max_pyrite law_5  min_pyrite law_5  \
Timestamp                                                           
2020-06-01               0.82              0.82              0.82   

            rms_pyrite law_5  var_pyrite law_5  mean_pyrite law_3  \
Timestamp                                                           
2020-06-01              0.82               0.0               0.82   

            max_pyrite law_3  min_pyrite law_3  rms_pyrite law_3  \
Timestamp                                                          
2020-06-01              0.82              0.82              0.82   

            var_pyrite law_3  mean_chalcopyrite law_10  \
Timestamp                                                
2020-06-01               0.0         

In [28]:
# Test
test=pd.concat([df_features["2020-04"],df_features["2021-09"],df_features["2022"]])
test.head(1)

sag power index  mean_sag power index_10  max_sag power index_10  \
Timestamp                                                                      
2020-04-01         116.3165                116.92157                116.9888   

            min_sag power index_10  rms_sag power index_10  \
Timestamp                                                    
2020-04-01                116.3165              116.921744   

            var_sag power index_10  mean_sag power index_5  \
Timestamp                                                    
2020-04-01                0.040679               116.85434   

            max_sag power index_5  min_sag power index_5  \
Timestamp                                                  
2020-04-01               116.9888               116.3165   

            rms_sag power index_5  var_sag power index_5  \
Timestamp                                                  
2020-04-01             116.854649               0.072318   

            mean_sag power index_3  max_sag power index_3  \
Timestamp                                                   
2020-04-01                116.7647               116.9888   

            min_sag power index_3  rms_sag power index_3  \
Timestamp                                                  
2020-04-01               116.3165              116.76513   

            var_sag power index_3  sag power index_(t-1)  \
Timestamp                                                  
2020-04-01               0.100442               116.9888   

            sag power index_(t-2)  sag power index_(t-3)  \
Timestamp                                                  
2020-04-01               116.9888               116.9888   

            sag power index_(t-4)  sag power index_(t-5)  pyrite law  \
Timestamp                                                              
2020-04-01               116.9888               116.9888        2.84   

            chalcopyrite law  chalcocite law  covelin law  crusher index  \
Timestamp                                                                  
2020-04-01              1.53            0.54         0.03        20.9675   

            ball work index  bornite law  charge cell          TPH     speed  \
Timestamp                                                                      
2020-04-01          17.0169         0.02    755.74875  4188.172694  9.249551   

            HH TPH  granulometry  loss of TPH  solid percentage  \
Timestamp                                                         
2020-04-01  3800.0     30.530144          0.0          65.03294   

            HH charge cell  LL charge cell  delta HH charge cell  \
Timestamp                                                          
2020-04-01           840.0           760.0              84.25125   

            delta LL charge cell  mean_pyrite law_10  max_pyrite law_10  \
Timestamp                                                                 
2020-04-01              -4.25125               2.957               2.97   

            min_pyrite law_10  rms_pyrite law_10  var_pyrite law_10  \
Timestamp                                                             
2020-04-01               2.84           2.957257           0.001521   

            mean_pyrite law_5  max_pyrite law_5  min_pyrite law_5  \
Timestamp                                                           
2020-04-01              2.944              2.97              2.84   

            rms_pyrite law_5  var_pyrite law_5  mean_pyrite law_3  \
Timestamp                                                           
2020-04-01          2.944459          0.002704           2.926667   

            max_pyrite law_3  min_pyrite law_3  rms_pyrite law_3  \
Timestamp                                                          
2020-04-01              2.97              2.84          2.927308   

            var_pyrite law_3  mean_chalcopyrite law_10  \
Timestamp                                                
2020-04-01          0.003756         

In [29]:
tags=df_features.columns.to_list()
tags.remove("loss of TPH")
#tags.remove("TPH")

In [30]:
# Sobremuestreo: Aumentar numero de datos de la clase minoritaria
# ROS(Duplica clases):
ros=RandomOverSampler(random_state=0) # Random_state=0

# ROS:
Xtrain, Ytrain=ros.fit_resample(entrenamiento[tags],entrenamiento["loss of TPH"])

In [31]:
# Ytrain reg
Ytrain=Xtrain["TPH"]
Xtrain=Xtrain.drop(columns=["TPH"])

In [32]:
# Yval reg
Yval=validacion["TPH"]
Xval=validacion.drop(columns=["TPH"])

In [33]:
Ytest0=test[test["loss of TPH"]==0]["TPH"]


In [34]:
Ytest1=test[test["loss of TPH"]==1]["TPH"]


In [35]:
Xtest0=test[test["loss of TPH"]==0].drop(columns=["TPH","loss of TPH"])


In [36]:
Xtest1=test[test["loss of TPH"]==1].drop(columns=["TPH","loss of TPH"])


In [37]:
# Ytest reg
Ytest=test["TPH"]
Xtest=test.drop(columns=["TPH"])

In [38]:
#Unión del conjunto de Entrenamiento y Validación:
Entre_Vali_features=pd.concat([Xval,Xtrain])
Entre_Vali_target=pd.concat([Yval,Ytrain])

#Indices para separar ambos conjuntos:
Entre_indice=np.full(len(validacion),-1)
Vali_indice=np.full(len(entrenamiento),0)
Indices=np.append(Entre_indice,Vali_indice)
x=PredefinedSplit(Indices)

In [39]:
Color_loss=test["loss of TPH"]
Color_loss=Color_loss.astype(str)

# Feature selection

In [40]:
# Preprocesamiento de datos

preprocessing_transformer = ColumnTransformer(
    transformers=[
        ('MinMax', MinMaxScaler(),
        Xtrain.columns.to_list()
        ),
    ])

pipe = Pipeline(
    [
        ("preprocesamiento", preprocessing_transformer), 
     ("clf", xgb.XGBRegressor(seed=1,eval_metric='rmse'
     ))
    ]
)

In [41]:
pipe.fit(Xtrain, Ytrain)

Pipeline(steps=[('preprocesamiento',
                 ColumnTransformer(transformers=[('MinMax', MinMaxScaler(),
                                                  ['sag power index',
                                                   'mean_sag power index_10',
                                                   'max_sag power index_10',
                                                   'min_sag power index_10',
                                                   'rms_sag power index_10',
                                                   'var_sag power index_10',
                                                   'mean_sag power index_5',
                                                   'max_sag power index_5',
                                                   'min_sag power index_5',
                                                   'rms_sag power index_5',
                                                   'var_sag power index_5',
                                                  

**General**

In [42]:
Ypred= pipe.predict(Xtest)

# Métricas
print('R2: ',r2_score(Ytest, Ypred),'\n','RMSE: ',mean_squared_error(Ytest, Ypred, squared=False))

R2:  0.546362448171696 
 RMSE:  284.7611051630667


In [43]:
df_importance=pd.DataFrame({"tag":Xtrain.columns,"importance":pipe["clf"].feature_importances_}).sort_values(by="importance",ascending=False).reset_index(drop=True)
df_importance.head()

tag  importance
0                   HH TPH    0.055092
1              min_speed_5    0.045803
2  min_solid percentage_10    0.040233
3   min_solid percentage_5    0.034294
4   min_solid percentage_3    0.033921

In [44]:
pd.options.plotting.backend = "plotly"
fig=df_importance["importance"].plot(kind='hist')
fig.update_layout(height=500, width=1200,title="Feature importance XGBoost (Gain)",) 
fig.show()

In [45]:
# Plot
fig = go.Figure([go.Bar(x=df_importance["tag"], y=df_importance["importance"])])
fig.update_layout(height=500, width=1200,title="Feature importance XGBoost (Gain)",) 
fig.show()

In [46]:
xgboost_fs=df_importance[:100].tag.to_list()
xgboost_fs

['HH TPH',
 'min_speed_5',
 'min_solid percentage_10',
 'min_solid percentage_5',
 'min_solid percentage_3',
 'max_delta LL charge cell_3',
 'chalcocite law_(t-3)',
 'min_speed_3',
 'rms_delta LL charge cell_3',
 'max_chalcopyrite law_3',
 'min_delta LL charge cell_10',
 'rms_sag power index_10',
 'bornite law_(t-5)',
 'rms_sag power index_3',
 'rms_solid percentage_5',
 'solid percentage',
 'min_HH charge cell_10',
 'max_ball work index_5',
 'rms_chalcopyrite law_5',
 'speed',
 'rms_delta LL charge cell_10',
 'var_bornite law_3',
 'LL charge cell_(t-5)',
 'max_sag power index_10',
 'min_sag power index_5',
 'min_chalcocite law_5',
 'mean_crusher index_5',
 'max_delta HH charge cell_10',
 'chalcopyrite law_(t-3)',
 'max_HH charge cell_10',
 'covelin law_(t-4)',
 'rms_crusher index_10',
 'rms_bornite law_10',
 'max_bornite law_5',
 'sag power index_(t-5)',
 'rms_chalcocite law_10',
 'rms_crusher index_5',
 'rms_chalcopyrite law_10',
 'min_speed_10',
 'min_chalcocite law_10',
 'min_LL ch

In [47]:
# Se obtienen tags altamente correlacionados y matriz que permite visualizar cuales son los par de tags altamente correlacionados
collinearity, table_cor=corrkill(Xtrain,xgboost_fs,corr_cut=0.9)

In [48]:
# Tags altamente correlacionados
table_cor

Feat1                        Feat2       Val
4660      rms_solid percentage_10     mean_solid percentage_10  0.999998
1382        rms_sag power index_3       mean_sag power index_3  0.999994
2636         mean_crusher index_5          rms_crusher index_5  0.999990
1027  min_delta LL charge cell_10  max_delta HH charge cell_10  0.999988
7984         delta HH charge cell         delta LL charge cell  0.999988
...                           ...                          ...       ...
1043  min_delta LL charge cell_10   rms_delta HH charge cell_3  0.906956
4195   rms_delta HH charge cell_5   delta HH charge cell_(t-5)  0.904327
4181   rms_delta HH charge cell_5   delta LL charge cell_(t-5)  0.904320
8793  min_delta HH charge cell_10   max_delta HH charge cell_5  0.904018
6193  max_delta LL charge cell_10   max_delta HH charge cell_5  0.903980

[303 rows x 3 columns]

In [49]:
tag_select = [i for i in xgboost_fs if i not in collinearity]
tag_select

['HH TPH',
 'min_speed_5',
 'min_solid percentage_10',
 'max_delta LL charge cell_3',
 'chalcocite law_(t-3)',
 'rms_delta LL charge cell_3',
 'max_chalcopyrite law_3',
 'rms_sag power index_10',
 'bornite law_(t-5)',
 'min_HH charge cell_10',
 'max_ball work index_5',
 'var_bornite law_3',
 'mean_crusher index_5',
 'covelin law_(t-4)',
 'min_charge cell_10',
 'min_granulometry_3',
 'var_solid percentage_3',
 'age tph processed',
 'pyrite law_(t-5)',
 'var_crusher index_3',
 'var_delta LL charge cell_3']

In [ ]:
tag_select=tag_select+["age tph processed"]

In [50]:
# Preprocesamiento de datos

preprocessing_transformer = ColumnTransformer(
    transformers=[
        ('MinMax', MinMaxScaler(),
        tag_select
        ),
    ])

pipe = Pipeline(
    [
        ("preprocesamiento", preprocessing_transformer), 
     ("clf", xgb.XGBRegressor(seed=1,eval_metric='rmse'
     ))
    ]
)

In [51]:
pipe.fit(Xtrain, Ytrain)

Pipeline(steps=[('preprocesamiento',
                 ColumnTransformer(transformers=[('MinMax', MinMaxScaler(),
                                                  ['HH TPH', 'min_speed_5',
                                                   'min_solid percentage_10',
                                                   'max_delta LL charge cell_3',
                                                   'chalcocite law_(t-3)',
                                                   'rms_delta LL charge cell_3',
                                                   'max_chalcopyrite law_3',
                                                   'rms_sag power index_10',
                                                   'bornite law_(t-5)',
                                                   'min_HH charge cell_10',
                                                   'max_ball work index_5',
                                                   'var_bornite law_3',
                                              

**General**

In [52]:
Ypred= pipe.predict(Xtest)

# Métricas
print('R2: ',r2_score(Ytest, Ypred),'\n','RMSE: ',mean_squared_error(Ytest, Ypred, squared=False))

R2:  0.5343520191098021 
 RMSE:  288.50612178540666


# GridSearch

In [53]:
# Preprocesamiento de datos

preprocessing_transformer = ColumnTransformer(
    transformers=[
        ('MinMax', MinMaxScaler(),
        tag_select
        #features.columns.to_list()
        ),
    ])

pipe = Pipeline(
    [
        ("preprocesamiento", preprocessing_transformer), 
        #("Selection", SelectPercentile(f_classif, percentile=10)),
        #("PCA",PCA(n_components=150 )), #0.08
     ("reg", xgb.XGBRegressor(seed=1,eval_metric='rmse'))
    ]
)


param_grid_reg = {'reg__learning_rate': list(np.linspace(0.001,1,10)), # Boosting learning rate
                  'reg__gamma':list(np.linspace(0.0001,50,5)), # Minimum loss reduction required to make a further partition on a leaf node of the tree.
                  #'reg__max_depth':[5,10,12,15,20], # Maximum tree depth for base learners.
                  #'reg__min_child_weight':[10,5,1,2,3], # Minimum sum of instance weight(hessian) needed in a child.
                  #'reg__colsample_bytree':[0.5,0.8,1], # Subsample ratio of columns when constructing each tree.
                  'reg__n_estimators': [100,200,300], # Number of gradient boosted trees.   
                  #'reg__reg_alpha': [0,0.1,0.2,0.4,0.8,1.6,3.2,6.4,12.8,25.6,51.2,102.4,200],
              #'reg__reg_lambda': [0,0.1,0.2,0.4,0.8,1.6,3.2,6.4,12.8,25.6,51.2,102.4,200],
               #'Selection__percentile': [10,20,30,50,70,80,100]              
                 } 

# Clasificación
gs_reg = HalvingGridSearchCV(pipe, param_grid_reg, scoring='neg_mean_absolute_error',cv=x,refit=True,
                             verbose=10,
                             aggressive_elimination=True
                            )

# Fit
gs_reg.fit(Entre_Vali_features, Entre_Vali_target)


n_iterations: 5
n_required_iterations: 5
n_possible_iterations: 5
min_resources_: 12955
max_resources_: 1049417
aggressive_elimination: True
factor: 3
----------
iter: 0
n_candidates: 150
n_resources: 12955
Fitting 1 folds for each of 150 candidates, totalling 150 fits
[CV 1/1; 1/150] START reg__gamma=0.0001, reg__learning_rate=0.001, reg__n_estimators=100
[CV 1/1; 1/150] END reg__gamma=0.0001, reg__learning_rate=0.001, reg__n_estimators=100;, score=(train=-3629.923, test=-3768.849) total time=   5.0s
[CV 1/1; 2/150] START reg__gamma=0.0001, reg__learning_rate=0.001, reg__n_estimators=200
[CV 1/1; 2/150] END reg__gamma=0.0001, reg__learning_rate=0.001, reg__n_estimators=200;, score=(train=-3286.068, test=-3429.369) total time=   0.4s
[CV 1/1; 3/150] START reg__gamma=0.0001, reg__learning_rate=0.001, reg__n_estimators=300
[CV 1/1; 3/150] END reg__gamma=0.0001, reg__learning_rate=0.001, reg__n_estimators=300;, score=(train=-2975.252, test=-3121.966) total time=   0.6s
[CV 1/1; 4/150] STA

HalvingGridSearchCV(aggressive_elimination=True,
                    cv=PredefinedSplit(test_fold=array([-1, -1, ...,  0,  0])),
                    estimator=Pipeline(steps=[('preprocesamiento',
                                               ColumnTransformer(transformers=[('MinMax',
                                                                                MinMaxScaler(),
                                                                                ['HH '
                                                                                 'TPH',
                                                                                 'min_speed_5',
                                                                                 'min_solid '
                                                                                 'percentage_10',
                                                                                 'max_delta '
                                                             

In [55]:
gs_reg.best_score_

-315.06881390289936

In [56]:
gs_reg.best_params_

{'reg__gamma': 25.000049999999998,
 'reg__learning_rate': 0.223,
 'reg__n_estimators': 100}

In [57]:
# General
Ypred= gs_reg.predict(Xtest)
# Métricas
print('R2: ',r2_score(Ytest, Ypred),'\n','RMSE: ',mean_squared_error(Ytest, Ypred, squared=False))

R2:  0.5779043948609122 
 RMSE:  274.6828760043008


# Train model

In [59]:
tag_select=['HH TPH',
 'min_speed_5',
 'min_solid percentage_10',
 'max_delta LL charge cell_3',
 'chalcocite law_(t-3)',
 'rms_delta LL charge cell_3',
 'max_chalcopyrite law_3',
 'rms_sag power index_10',
 'bornite law_(t-5)',
 'min_HH charge cell_10',
 'max_ball work index_5',
 'var_bornite law_3',
 'mean_crusher index_5',
 'covelin law_(t-4)',
 'min_charge cell_10',
 'min_granulometry_3',
 'var_solid percentage_3',
 'age tph processed',
 'pyrite law_(t-5)',
 'var_crusher index_3',
 'var_delta LL charge cell_3']

In [60]:
gs_reg.best_params_

{'reg__gamma': 25.000049999999998,
 'reg__learning_rate': 0.223,
 'reg__n_estimators': 100}

In [61]:
# Preprocesamiento de datos

preprocessing_transformer = ColumnTransformer(
    transformers=[
        ('MinMax', MinMaxScaler(),
        tag_select
        ),
    ])

pipe = Pipeline(
    [
        ("preprocesamiento", preprocessing_transformer), 
     ("clf", xgb.XGBRegressor(seed=1,eval_metric='rmse',gamma= 25, learning_rate= 0.223, n_estimators= 100
     
     ))
    ]
)
pipe.fit(Xtrain, Ytrain)

Pipeline(steps=[('preprocesamiento',
                 ColumnTransformer(transformers=[('MinMax', MinMaxScaler(),
                                                  ['HH TPH', 'min_speed_5',
                                                   'min_solid percentage_10',
                                                   'max_delta LL charge cell_3',
                                                   'chalcocite law_(t-3)',
                                                   'rms_delta LL charge cell_3',
                                                   'max_chalcopyrite law_3',
                                                   'rms_sag power index_10',
                                                   'bornite law_(t-5)',
                                                   'min_HH charge cell_10',
                                                   'max_ball work index_5',
                                                   'var_bornite law_3',
                                              

**General**

In [62]:
# General
Ypred= pipe.predict(Xtest0)
# Métricas
print('R2: ',r2_score(Ytest0, Ypred),'\n','RMSE: ',mean_squared_error(Ytest0, Ypred, squared=False))

R2:  0.5001160874902445 
 RMSE:  197.59674526646359


In [63]:
# General
Ypred= pipe.predict(Xtest1)
# Métricas
print('R2: ',r2_score(Ytest1, Ypred),'\n','RMSE: ',mean_squared_error(Ytest1, Ypred, squared=False))

R2:  0.2860137456827301 
 RMSE:  424.4350432881479


In [64]:
Ypred= pipe.predict(Xtest)
# Métricas
print('R2: ',r2_score(Ytest, Ypred),'\n','RMSE: ',mean_squared_error(Ytest, Ypred, squared=False),'\n','MAPE :',mean_absolute_percentage_error(Ytest, Ypred)*100)

R2:  0.5802978590447132 
 RMSE:  273.90298364500114 
 MAPE : 4.722395354586433


In [24]:
Ypred= pipe.predict(Xtest)
# Métricas
print('R2: ',r2_score(Ytest, Ypred),'\n','RMSE: ',mean_squared_error(Ytest, Ypred, squared=False),'\n','MAPE :',mean_absolute_percentage_error(Ytest, Ypred)*100)

R2:  0.5814266261044121 
 RMSE:  273.5344117564454 
 MAPE : 4.753283702806609


In [65]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=Ypred[:10000], y=Ytest[:10000],
                    mode='markers',
                    name='(Pred,Test)'))

fig.add_trace(go.Scatter(x=[i for i in range(2500,4700)], y=[i for i in range(2500,4700)],
                    mode='markers', name='Identidad'))
                    
fig.update_layout(height=500, width=1200, title_text="Scatter predict/test", xaxis_title="Predict",
    yaxis_title="Test")
fig.show()

In [66]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(y=Ypred[:10000], 
                    mode='lines',name="predict"
                    ))

fig.add_trace(go.Scatter(y=Ytest[:10000],
                    mode='lines',name="Test",#marker=dict(color=list(Color_loss[:1000]))
                    ))

fig.update_layout(height=500, width=1200, title_text="TPH vs TPH predict")
fig.show()

**Histograma del error RMSE y desviación estandar**

In [67]:
(Ytest-Ypred).abs().std()

208.6699883258476

In [68]:
(Ytest-Ypred).abs().mean()

177.4260561673195

In [69]:
pd.options.plotting.backend = "plotly"
df_dist_error=pd.DataFrame()
df_dist_error["Error"]=(Ytest-Ypred)#.abs()
fig=df_dist_error["Error"].plot(kind='hist')
fig.update_layout(height=500, width=1200,title="Distribución Error RMSE") 
fig.show()

**2020**

In [ ]:
Ypred= pipe.predict(Xtest["2020"])

# Métricas
print('R2: ',r2_score(Ytest["2020"], Ypred),'\n','RMSE: ',mean_squared_error(Ytest["2020"], Ypred, squared=False))

**2021**

In [ ]:
Ypred= pipe.predict(Xtest["2021"])

# Métricas
print('R2: ',r2_score(Ytest["2021"], Ypred),'\n','RMSE: ',mean_squared_error(Ytest["2021"], Ypred, squared=False))

**2022**

In [ ]:
Ypred= pipe.predict(Xtest["2022-01"])

# Métricas
print('R2: ',r2_score(Ytest["2022-01"], Ypred),'\n','RMSE: ',mean_squared_error(Ytest["2022-01"], Ypred, squared=False))

In [ ]:
Ypred= pipe.predict(Xtest["2022-02"])

# Métricas
print('R2: ',r2_score(Ytest["2022-02"], Ypred),'\n','RMSE: ',mean_squared_error(Ytest["2022-02"], Ypred, squared=False))

# Simulation time series predict

# 2020

In [ ]:
# test 2021
test_time_serie=Xtest["2020"]
test_time_serie["TPH"]=Ytest["2020"]
test_time_serie["TPH predict"]=pipe.predict(test_time_serie)


# Métricas
print('R2: ',r2_score(test_time_serie["TPH"], test_time_serie["TPH predict"]),'\n','RMSE: ',mean_squared_error(test_time_serie["TPH"], test_time_serie["TPH predict"], squared=False))
test_time_serie["TPH"]=test_time_serie["TPH"].shift(10)
test_time_serie.dropna(inplace=True)
data=test_time_serie
data.head(1)

In [ ]:
titulos=tuple(["TPH & HH TPH", "charge cell","granulometry","SPI","speed","solid percentage"])
fig = make_subplots(
    rows=6, cols=1,
    subplot_titles=titulos,
    #subplot_titles=tuple("TPH y HH TPH,"),
     shared_xaxes=True
    )


fig.add_trace(go.Scatter(x=data.index, y=data['TPH'], ##FF6511
                    mode='lines',
                    name="TPH",line=dict(width=3, ),legendgroup = '1'),row=1, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['TPH predict'], ##FF6511
                    mode='lines',
                    name="TPH predict",line=dict(width=3, ),legendgroup = '1'),row=1, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['HH TPH'], ##FF6511
                    mode='lines',
                    name="HH TPH",line=dict(width=3, ),legendgroup = '1'),row=1, col=1)  

#fig.add_trace(go.Scatter(x=data.index, y=data["TPH predict"], ##FF6511
#                    mode='lines',
#                    name="regressor model TPH",line=dict(width=1,color="black" ),legendgroup = '1'),row=1, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['charge cell'], 
                    mode='lines',
                    name="charge cell",line=dict(width=3, ),legendgroup = '1'),row=2, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['HH charge cell'], 
                    mode='lines',
                    name="charge cell",line=dict(width=3, ),legendgroup = '1'),row=2, col=1) 

fig.add_trace(go.Scatter(x=data.index, y=data['LL charge cell'], 
                    mode='lines',
                    name="charge cell",line=dict(width=3, ),legendgroup = '1'),row=2, col=1)   

fig.add_trace(go.Scatter(x=data.index, y=data['granulometry'], ##FF6511
                    mode='lines',
                    name='granulometry',line=dict(width=3,),legendgroup = '1'),row=3, col=1)  


fig.add_trace(go.Scatter(x=data.index, y=data['sag power index'], ##FF6511
                    mode='lines',
                    name="sag power index",line=dict(width=3, ),legendgroup = '1'),row=4, col=1)  



fig.add_trace(go.Scatter(x=data.index, y=data['speed'], ##FF6511
                    mode='lines',
                    name="speed",line=dict(width=3, ),legendgroup = '1'),row=5, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['solid percentage'], ##FF6511
                    mode='lines',
                    name='solid percentage',line=dict(width=3, ),legendgroup = '1'),row=6, col=1)  


#for i in range(1,6):
#   for j in range(1,4):
#        fig.update_xaxes(tickformat="%H:%M",row=i, col=j)


fig.update_layout(height=1000, width=1500, title_text="Temporal signal analysis")
fig.update_layout(hovermode="x unified")
#

fig.show()

In [ ]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=data.index, y=data["TPH"],
                    mode='lines',
                    name='TPH'))
fig.add_trace(go.Scatter(x=data.index, y=data["TPH predict"],
                    mode='lines',
                    name='TPH predict'))

fig.add_trace(go.Scatter(x=data.index, y=data["HH TPH"],
                    mode='lines',
                    name='HH TPH'))

fig.update_layout(height=500, width=1200, title_text="TPH vs TPH predict"#,xaxis6_rangeslider_visible=True
,#template="plotly_dark"
)                   
fig.show()

In [ ]:
fig.write_html("file.html")

# 2021

In [ ]:
# test 2021
test_time_serie=Xtest["2021"]
test_time_serie["TPH"]=Ytest["2021"]
test_time_serie["TPH predict"]=pipe.predict(test_time_serie)


# Métricas
print('R2: ',r2_score(test_time_serie["TPH"], test_time_serie["TPH predict"]),'\n','RMSE: ',mean_squared_error(test_time_serie["TPH"], test_time_serie["TPH predict"], squared=False))
test_time_serie["TPH"]=test_time_serie["TPH"].shift(10)
test_time_serie.dropna(inplace=True)
data=test_time_serie
data.head(1)

In [ ]:
titulos=tuple(["TPH & HH TPH", "charge cell","granulometry","SPI","speed","solid percentage"])
fig = make_subplots(
    rows=6, cols=1,
    subplot_titles=titulos,
    #subplot_titles=tuple("TPH y HH TPH,"),
     shared_xaxes=True
    )


fig.add_trace(go.Scatter(x=data.index, y=data['TPH'], ##FF6511
                    mode='lines',
                    name="TPH",line=dict(width=3, ),legendgroup = '1'),row=1, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['TPH predict'], ##FF6511
                    mode='lines',
                    name="TPH predict",line=dict(width=3, ),legendgroup = '1'),row=1, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['HH TPH'], ##FF6511
                    mode='lines',
                    name="HH TPH",line=dict(width=3, ),legendgroup = '1'),row=1, col=1)  

#fig.add_trace(go.Scatter(x=data.index, y=data["TPH predict"], ##FF6511
#                    mode='lines',
#                    name="regressor model TPH",line=dict(width=1,color="black" ),legendgroup = '1'),row=1, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['charge cell'], 
                    mode='lines',
                    name="charge cell",line=dict(width=3, ),legendgroup = '1'),row=2, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['HH charge cell'], 
                    mode='lines',
                    name="charge cell",line=dict(width=3, ),legendgroup = '1'),row=2, col=1) 

fig.add_trace(go.Scatter(x=data.index, y=data['LL charge cell'], 
                    mode='lines',
                    name="charge cell",line=dict(width=3, ),legendgroup = '1'),row=2, col=1)   

fig.add_trace(go.Scatter(x=data.index, y=data['granulometry'], ##FF6511
                    mode='lines',
                    name='granulometry',line=dict(width=3,),legendgroup = '1'),row=3, col=1)  


fig.add_trace(go.Scatter(x=data.index, y=data['sag power index'], ##FF6511
                    mode='lines',
                    name="sag power index",line=dict(width=3, ),legendgroup = '1'),row=4, col=1)  



fig.add_trace(go.Scatter(x=data.index, y=data['speed'], ##FF6511
                    mode='lines',
                    name="speed",line=dict(width=3, ),legendgroup = '1'),row=5, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['solid percentage'], ##FF6511
                    mode='lines',
                    name='solid percentage',line=dict(width=3, ),legendgroup = '1'),row=6, col=1)  


#for i in range(1,6):
#   for j in range(1,4):
#        fig.update_xaxes(tickformat="%H:%M",row=i, col=j)


fig.update_layout(height=1000, width=1500, title_text="Temporal signal analysis")
fig.update_layout(hovermode="x unified")
#

fig.show()

In [ ]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=data.index, y=data["TPH"],
                    mode='lines',
                    name='TPH'))
fig.add_trace(go.Scatter(x=data.index, y=data["TPH predict"],
                    mode='lines',
                    name='TPH predict'))

fig.add_trace(go.Scatter(x=data.index, y=data["HH TPH"],
                    mode='lines',
                    name='HH TPH'))

fig.update_layout(height=500, width=1200, title_text="TPH vs TPH predict"#,xaxis6_rangeslider_visible=True
,#template="plotly_dark"
)                   
fig.show()

# 2022

In [ ]:
# test 2022-01
test_time_serie=Xtest["2022-01"]
test_time_serie["TPH"]=Ytest["2022-01"]
test_time_serie["TPH predict"]=pipe.predict(test_time_serie)


# Métricas
print('R2: ',r2_score(test_time_serie["TPH"], test_time_serie["TPH predict"]),'\n','RMSE: ',mean_squared_error(test_time_serie["TPH"], test_time_serie["TPH predict"], squared=False))
test_time_serie["TPH"]=test_time_serie["TPH"].shift(10)
test_time_serie.dropna(inplace=True)
data=test_time_serie
data.head(1)

In [ ]:
titulos=tuple(["TPH & HH TPH", "charge cell","granulometry","SPI","speed","solid percentage"])
fig = make_subplots(
    rows=6, cols=1,
    subplot_titles=titulos,
    #subplot_titles=tuple("TPH y HH TPH,"),
     shared_xaxes=True
    )


fig.add_trace(go.Scatter(x=data.index, y=data['TPH'], ##FF6511
                    mode='lines',
                    name="TPH",line=dict(width=3, ),legendgroup = '1'),row=1, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['TPH predict'], ##FF6511
                    mode='lines',
                    name="TPH predict",line=dict(width=3, ),legendgroup = '1'),row=1, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['HH TPH'], ##FF6511
                    mode='lines',
                    name="HH TPH",line=dict(width=3, ),legendgroup = '1'),row=1, col=1)  

#fig.add_trace(go.Scatter(x=data.index, y=data["TPH predict"], ##FF6511
#                    mode='lines',
#                    name="regressor model TPH",line=dict(width=1,color="black" ),legendgroup = '1'),row=1, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['charge cell'], 
                    mode='lines',
                    name="charge cell",line=dict(width=3, ),legendgroup = '1'),row=2, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['HH charge cell'], 
                    mode='lines',
                    name="charge cell",line=dict(width=3, ),legendgroup = '1'),row=2, col=1) 

fig.add_trace(go.Scatter(x=data.index, y=data['LL charge cell'], 
                    mode='lines',
                    name="charge cell",line=dict(width=3, ),legendgroup = '1'),row=2, col=1)   

fig.add_trace(go.Scatter(x=data.index, y=data['granulometry'], ##FF6511
                    mode='lines',
                    name='granulometry',line=dict(width=3,),legendgroup = '1'),row=3, col=1)  


fig.add_trace(go.Scatter(x=data.index, y=data['sag power index'], ##FF6511
                    mode='lines',
                    name="sag power index",line=dict(width=3, ),legendgroup = '1'),row=4, col=1)  



fig.add_trace(go.Scatter(x=data.index, y=data['speed'], ##FF6511
                    mode='lines',
                    name="speed",line=dict(width=3, ),legendgroup = '1'),row=5, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['solid percentage'], ##FF6511
                    mode='lines',
                    name='solid percentage',line=dict(width=3, ),legendgroup = '1'),row=6, col=1)  


#for i in range(1,6):
#   for j in range(1,4):
#        fig.update_xaxes(tickformat="%H:%M",row=i, col=j)


fig.update_layout(height=1000, width=1500, title_text="Temporal signal analysis")
fig.update_layout(hovermode="x unified")
#

fig.show()

In [ ]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=data.index, y=data["TPH"],
                    mode='lines',
                    name='TPH'))
fig.add_trace(go.Scatter(x=data.index, y=data["TPH predict"],
                    mode='lines',
                    name='TPH predict'))

fig.add_trace(go.Scatter(x=data.index, y=data["HH TPH"],
                    mode='lines',
                    name='HH TPH'))

fig.update_layout(height=500, width=1200, title_text="TPH vs TPH predict"#,xaxis6_rangeslider_visible=True
,#template="plotly_dark"
)                   
fig.show()

In [ ]:
# test 2022-02
test_time_serie=Xtest["2022-02"]
test_time_serie["TPH"]=Ytest["2022-02"]
test_time_serie["TPH predict"]=pipe.predict(test_time_serie)


# Métricas
print('R2: ',r2_score(test_time_serie["TPH"], test_time_serie["TPH predict"]),'\n','RMSE: ',mean_squared_error(test_time_serie["TPH"], test_time_serie["TPH predict"], squared=False))
test_time_serie["TPH"]=test_time_serie["TPH"].shift(10)
test_time_serie.dropna(inplace=True)
data=test_time_serie
data.head(1)

In [ ]:
titulos=tuple(["TPH & HH TPH", "charge cell","granulometry","SPI","speed","solid percentage"])
fig = make_subplots(
    rows=6, cols=1,
    subplot_titles=titulos,
    #subplot_titles=tuple("TPH y HH TPH,"),
     shared_xaxes=True
    )


fig.add_trace(go.Scatter(x=data.index, y=data['TPH'], ##FF6511
                    mode='lines',
                    name="TPH",line=dict(width=3, ),legendgroup = '1'),row=1, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['TPH predict'], ##FF6511
                    mode='lines',
                    name="TPH predict",line=dict(width=3, ),legendgroup = '1'),row=1, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['HH TPH'], ##FF6511
                    mode='lines',
                    name="HH TPH",line=dict(width=3, ),legendgroup = '1'),row=1, col=1)  

#fig.add_trace(go.Scatter(x=data.index, y=data["TPH predict"], ##FF6511
#                    mode='lines',
#                    name="regressor model TPH",line=dict(width=1,color="black" ),legendgroup = '1'),row=1, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['charge cell'], 
                    mode='lines',
                    name="charge cell",line=dict(width=3, ),legendgroup = '1'),row=2, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['HH charge cell'], 
                    mode='lines',
                    name="charge cell",line=dict(width=3, ),legendgroup = '1'),row=2, col=1) 

fig.add_trace(go.Scatter(x=data.index, y=data['LL charge cell'], 
                    mode='lines',
                    name="charge cell",line=dict(width=3, ),legendgroup = '1'),row=2, col=1)   

fig.add_trace(go.Scatter(x=data.index, y=data['granulometry'], ##FF6511
                    mode='lines',
                    name='granulometry',line=dict(width=3,),legendgroup = '1'),row=3, col=1)  


fig.add_trace(go.Scatter(x=data.index, y=data['sag power index'], ##FF6511
                    mode='lines',
                    name="sag power index",line=dict(width=3, ),legendgroup = '1'),row=4, col=1)  



fig.add_trace(go.Scatter(x=data.index, y=data['speed'], ##FF6511
                    mode='lines',
                    name="speed",line=dict(width=3, ),legendgroup = '1'),row=5, col=1)  

fig.add_trace(go.Scatter(x=data.index, y=data['solid percentage'], ##FF6511
                    mode='lines',
                    name='solid percentage',line=dict(width=3, ),legendgroup = '1'),row=6, col=1)  


#for i in range(1,6):
#   for j in range(1,4):
#        fig.update_xaxes(tickformat="%H:%M",row=i, col=j)


fig.update_layout(height=1000, width=1500, title_text="Temporal signal analysis")
fig.update_layout(hovermode="x unified")
#

fig.show()

In [ ]:
# Create traces
fig = go.Figure()
fig.add_trace(go.Scatter(x=data.index, y=data["TPH"],
                    mode='lines',
                    name='TPH'))
fig.add_trace(go.Scatter(x=data.index, y=data["TPH predict"],
                    mode='lines',
                    name='TPH predict'))

fig.add_trace(go.Scatter(x=data.index, y=data["HH TPH"],
                    mode='lines',
                    name='HH TPH'))

fig.update_layout(height=500, width=1200, title_text="TPH vs TPH predict"#,xaxis6_rangeslider_visible=True
,#template="plotly_dark"
)                   
fig.show()